In [177]:
import pickle
import pandas as pd
import numpy as np
#from sklearn.neural_network import MLPClassifier
from sklearn.metrics.pairwise import *
from sklearn import linear_model
from scipy.optimize import linear_sum_assignment

### Load a dataframe representing bodies and face information

In [85]:
bodyFace = pd.read_pickle('bodyFace')

In [86]:
bodyFace.head()

traSeq  trackId  trackX  trackY  trackW  trackH    height  distance  \
seq  id                                                                        
4793 4     4793        4   326.4   124.0   387.6   458.0  1.571027  2.248792   
     5     4793        5   802.4   150.0   442.0   520.0  1.519628  1.882822   
     6     4793        6  1135.6   108.0   309.4   364.0  1.475796  2.760290   
     7     4793        7   822.8   108.0    88.4   104.0  1.050643  6.857205   
4794 4     4794        4   323.0   124.0   387.6   456.0  1.569231  2.253340   

         rgbSeq        blur                                          embedding  
seq  id                                                                         
4793 4       22  367.316834  [-0.110296, 0.0504573, 0.00468473, -0.0105098,...  
     5       22  790.153174  [0.0554316, 0.0860607, -0.00389893, 0.0320879,...  
     6       22  600.989129  [-0.0656685, 0.047579, -0.100778, 0.00661445, ...  
     7       22         NaN  [None, None, None, None, None, None, None, Non...  
4794 4       23  367.316834  [-0.110296, 0.0504573, 0.00468473, -0.0105098,...

Should extract embedding into columns of features

In [87]:
#Extract embedding informations and rearrange it into columns 
#(one column for each features - 128 columns in total)
em = [[] for i in range(len(bodyFace.iloc[0].embedding))]

for index, r in bodyFace.iterrows():
    for column in range (len(bodyFace.iloc[0].embedding)):
         em[column].append(r.embedding[column])
            
#Insert nex feature's columns into dataframe
for column in range (len(bodyFace.iloc[0].embedding)):
    bodyFace[column] = em[column]
    
bodyFace.drop('embedding', 1, inplace=True)

In [88]:
bodyFace.head()

traSeq  trackId  trackX  trackY  trackW  trackH    height  distance  \
seq  id                                                                        
4793 4     4793        4   326.4   124.0   387.6   458.0  1.571027  2.248792   
     5     4793        5   802.4   150.0   442.0   520.0  1.519628  1.882822   
     6     4793        6  1135.6   108.0   309.4   364.0  1.475796  2.760290   
     7     4793        7   822.8   108.0    88.4   104.0  1.050643  6.857205   
4794 4     4794        4   323.0   124.0   387.6   456.0  1.569231  2.253340   

         rgbSeq        blur    ...          118       119       120       121  \
seq  id                        ...                                              
4793 4       22  367.316834    ...    -0.001748 -0.086560  0.028729  0.066900   
     5       22  790.153174    ...    -0.033809 -0.125701  0.021227  0.139772   
     6       22  600.989129    ...    -0.025146 -0.081062  0.052214  0.186648   
     7       22         NaN    ...          NaN       NaN       NaN       NaN   
4794 4       23  367.316834    ...    -0.001748 -0.086560  0.028729  0.066900   

              122       123       124       125       126       127  
seq  id                                                              
4793 4  -0.051501 -0.029163  0.052923 -0.105883  0.100579 -0.002058  
     5  -0.022684 -0.037909  0.186199 -0.067317  0.077795  0.044126  
     6  -0.156097  0.029255  0.069186 -0.105391 -0.135352 -0.108049  
     7        NaN       NaN       NaN       NaN       NaN       NaN  
4794 4  -0.051501 -0.029163  0.052923 -0.105883  0.100579 -0.002058  

[5 rows x 138 columns]

Should remove NaN values

In [89]:
bodyFace.dropna(inplace=True)

In [90]:
bodyFace.drop(['traSeq', 'trackId', 'rgbSeq', 'trackX', 'trackY', 'trackW', 'trackH', 'distance', 'blur'],
              axis=1, inplace=True)

In [91]:
bodyFace.head()

height         0         1         2         3         4         5  \
seq  id                                                                         
4793 4   1.571027 -0.110296  0.050457  0.004685 -0.010510  0.090073 -0.030573   
     5   1.519628  0.055432  0.086061 -0.003899  0.032088  0.010968  0.021055   
     6   1.475796 -0.065669  0.047579 -0.100778  0.006614 -0.008296  0.045751   
4794 4   1.569231 -0.110296  0.050457  0.004685 -0.010510  0.090073 -0.030573   
     5   1.519507  0.055432  0.086061 -0.003899  0.032088  0.010968  0.021055   

                6         7         8    ...          118       119       120  \
seq  id                                  ...                                    
4793 4   0.046243  0.012463 -0.044837    ...    -0.001748 -0.086560  0.028729   
     5  -0.058148  0.038498  0.004551    ...    -0.033809 -0.125701  0.021227   
     6  -0.070146 -0.024674  0.138617    ...    -0.025146 -0.081062  0.052214   
4794 4   0.046243  0.012463 -0.044837    ...    -0.001748 -0.086560  0.028729   
     5  -0.058148  0.038498  0.004551    ...    -0.033809 -0.125701  0.021227   

              121       122       123       124       125       126       127  
seq  id                                                                        
4793 4   0.066900 -0.051501 -0.029163  0.052923 -0.105883  0.100579 -0.002058  
     5   0.139772 -0.022684 -0.037909  0.186199 -0.067317  0.077795  0.044126  
     6   0.186648 -0.156097  0.029255  0.069186 -0.105391 -0.135352 -0.108049  
4794 4   0.066900 -0.051501 -0.029163  0.052923 -0.105883  0.100579 -0.002058  
     5   0.139772 -0.022684 -0.037909  0.186199 -0.067317  0.077795  0.044126  

[5 rows x 129 columns]

Create a dataframe of identity score for each name.
Each detection wil be compare to each identity in the database. The comparaison will result in a database with ID as index and identity score as column. The identity score is computed as the sum of the comparaison (+1 if the model return 1 and -1 if the model returns 0)
Id with only negative result will be consider as visitor.
Id with at least one positive result will be process to be attached to an identity (Hungarian algorithm).

In [92]:
# Import database of embeddings
database = pd.read_pickle('database')

# Need to modify columns order to have the same for every sample (from DB and from detection)
cols = database.columns.tolist()
cols = cols[-1:] + cols[:-1]
database = database[cols]

In [93]:
#database.head()

### Height nomalization

In [94]:
bodyFace.height = bodyFace.height.apply(lambda x : (x - 1.8)*2)

In [95]:
database.height = database.height.apply(lambda x : (x - 1.8)*2)

### Prepare data for MLP classifier

In [96]:
# load the model from disk
filename = 'svm.sav'
svm = pickle.load(open(filename, 'rb'))

In [97]:
#database.head()

In [98]:
score = [[] for i in range(len(database.index))]

for index, r in bodyFace.iterrows():
    i = 0
    temp = r
    for name, base in database.iterrows():
        cosines = cosine_similarity(np.asarray(base), np.asarray(temp.reshape(1, -1)))
        cosines = cosines.reshape(1, -1).squeeze()

        pred = svm.predict(cosines.reshape(1, -1))
        score[i].append(pred)
        i = i + 1

/home/sabrine/anaconda2/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: reshape is deprecated and will raise in a subsequent release. Please use .values.reshape(...) instead
/home/sabrine/anaconda2/lib/python2.7/site-packages/sklearn/utils/validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
/home/sabrine/anaconda2/lib/python2.7/site-packages/sklearn/utils/validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
/home/sabrine/anaconda2/lib/python2.7/site-packages/sklearn/utils/validation.py:395: DeprecationWarning: Passing 1d ar

In [100]:
data = np.asarray(score).squeeze().T
test = pd.DataFrame(data, columns=database.index)

In [101]:
len(test)

903

In [108]:
len(bodyFace)

903

In [102]:
test.sum()

Laurene      0.0
Laurene      0.0
Laurene      0.0
Wissem       0.0
Wissem       0.0
Wissem       0.0
Cynthia    301.0
Cynthia    301.0
Cynthia      0.0
Sabrine      2.0
Sabrine     48.0
Sabrine      4.0
Oliver     259.0
Oliver     560.0
Oliver     602.0
Lucas      386.0
Lucas      416.0
Lucas      500.0
Alberto    589.0
Alberto    760.0
Alberto    561.0
dtype: float64

In [126]:
max_ = [[] for i in range(len(test.columns.unique()))]
for index, name in enumerate(test.columns.unique()):
    print name
    sameName = test[name]
    max_[index] = sameName.max(axis=1) 

Laurene
Wissem
Cynthia
Sabrine
Oliver
Lucas
Alberto


In [149]:
predictions = pd.DataFrame(np.asarray(max_).T, columns=test.columns.unique())

In [196]:
bodyFaceBis = bodyFace.copy()
bodyFaceBis.reset_index(inplace=True)

In [197]:
identified = bodyFaceBis.join(predictions)
#identified.set_index(['seq', 'id'], inplace=True)

In [202]:
def cumsum_return(grp):
    grp[test.columns.unique()] = grp[test.columns.unique()].cumsum()
    return grp

In [205]:
identifiedSum = identified.groupby('id').apply(cumsum_return)

In [226]:
identifiedSum.head(10)

seq  id    height         0         1         2         3         4  \
0  4793   4 -0.457947 -0.110296  0.050457  0.004685 -0.010510  0.090073   
1  4793   5 -0.560744  0.055432  0.086061 -0.003899  0.032088  0.010968   
2  4793   6 -0.648407 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
3  4794   4 -0.461538 -0.110296  0.050457  0.004685 -0.010510  0.090073   
4  4794   5 -0.560986  0.055432  0.086061 -0.003899  0.032088  0.010968   
5  4794   6 -0.627961 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
6  4796   4 -0.464243 -0.110296  0.050457  0.004685 -0.010510  0.090073   
7  4796   5 -0.550689  0.055432  0.086061 -0.003899  0.032088  0.010968   
8  4796   6 -0.619520 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
9  4797   4 -0.468360 -0.110296  0.050457  0.004685 -0.010510  0.090073   

          5         6   ...          125       126       127  Laurene  Wissem  \
0 -0.030573  0.046243   ...    -0.105883  0.100579 -0.002058      0.0     0.0   
1  0.021055 -0.058148   ...    -0.067317  0.077795  0.044126      0.0     0.0   
2  0.045751 -0.070146   ...    -0.105391 -0.135352 -0.108049      0.0     0.0   
3 -0.030573  0.046243   ...    -0.105883  0.100579 -0.002058      0.0     0.0   
4  0.021055 -0.058148   ...    -0.067317  0.077795  0.044126      0.0     0.0   
5  0.045751 -0.070146   ...    -0.105391 -0.135352 -0.108049      0.0     0.0   
6 -0.030573  0.046243   ...    -0.105883  0.100579 -0.002058      0.0     0.0   
7  0.021055 -0.058148   ...    -0.067317  0.077795  0.044126      0.0     0.0   
8  0.045751 -0.070146   ...    -0.105391 -0.135352 -0.108049      0.0     0.0   
9 -0.030573  0.046243   ...    -0.105883  0.100579 -0.002058      0.0     0.0   

   Cynthia  Sabrine  Oliver  Lucas  Alberto  
0      0.0      0.0     1.0    1.0      0.0  
1      1.0      0.0     1.0    0.0      1.0  
2      0.0      0.0     1.0    1.0      1.0  
3      0.0      0.0     2.0    2.0      0.0  
4      2.0      0.0     2.0    0.0      2.0  
5      0.0      0.0     2.0    2.0      2.0  
6      0.0      0.0     3.0    3.0      0.0  
7      3.0      0.0     3.0    0.0      3.0  
8      0.0      0.0     3.0    3.0      3.0  
9      0.0      0.0     4.0    4.0      0.0  

[10 rows x 138 columns]

In [227]:
listAssignement = []
for seq, group in identifiedSum.groupby('seq'):
    negative = group[test.columns.unique()].multiply(-1)
    row_ind, col_ind = linear_sum_assignment(negative)
    for i in range(len(row_ind)):
        if abs(negative.iloc[row_ind[i], col_ind[i]]) > 2:
            #print 'legit'
            listAssignement.append(negative.columns[col_ind[i]])
        else:
            #print 'not legit'
            listAssignement.append(np.nan)
    #print group[test.columns.unique()].multiply(-1)


not legit
not legit
not legit
not legit
not legit
not legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
not legit
legit
legit
not legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
legit
le

In [228]:
identified['identity'] = pd.Series(np.asarray(listAssignement).T)

In [229]:
identified

seq  id    height         0         1         2         3         4  \
0    4793   4 -0.457947 -0.110296  0.050457  0.004685 -0.010510  0.090073   
1    4793   5 -0.560744  0.055432  0.086061 -0.003899  0.032088  0.010968   
2    4793   6 -0.648407 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
3    4794   4 -0.461538 -0.110296  0.050457  0.004685 -0.010510  0.090073   
4    4794   5 -0.560986  0.055432  0.086061 -0.003899  0.032088  0.010968   
5    4794   6 -0.627961 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
6    4796   4 -0.464243 -0.110296  0.050457  0.004685 -0.010510  0.090073   
7    4796   5 -0.550689  0.055432  0.086061 -0.003899  0.032088  0.010968   
8    4796   6 -0.619520 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
9    4797   4 -0.468360 -0.110296  0.050457  0.004685 -0.010510  0.090073   
10   4797   5 -0.557300  0.055432  0.086061 -0.003899  0.032088  0.010968   
11   4797   6 -0.619520 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
12   4798   4 -0.466472 -0.110296  0.050457  0.004685 -0.010510  0.090073   
13   4798   5 -0.563380  0.055432  0.086061 -0.003899  0.032088  0.010968   
14   4798   6 -0.614966 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
15   4799   4 -0.466088 -0.110296  0.050457  0.004685 -0.010510  0.090073   
16   4799   5 -0.569108  0.055432  0.086061 -0.003899  0.032088  0.010968   
17   4799   6 -0.614966 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
18   4800   4 -0.473479 -0.110296  0.050457  0.004685 -0.010510  0.090073   
19   4800   5 -0.574750  0.055432  0.086061 -0.003899  0.032088  0.010968   
20   4800   6 -0.614820 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
21   4801   4 -0.475258 -0.110296  0.050457  0.004685 -0.010510  0.090073   
22   4801   5 -0.576423  0.055432  0.086061 -0.003899  0.032088  0.010968   
23   4801   6 -0.612033 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
24   4803   4 -0.460827 -0.110296  0.050457  0.004685 -0.010510  0.090073   
25   4803   5 -0.586044  0.055432  0.086061 -0.003899  0.032088  0.010968   
26   4803   6 -0.601749 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
27   4804   4 -0.463611 -0.110296  0.050457  0.004685 -0.010510  0.090073   
28   4804   5 -0.586625  0.055432  0.086061 -0.003899  0.032088  0.010968   
29   4804   6 -0.603673 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
..    ...  ..       ...       ...       ...       ...       ...       ...   
873  5165   5 -0.633010  0.055432  0.086061 -0.003899  0.032088  0.010968   
874  5165   6 -0.709443 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
875  5165   9 -0.556295 -0.110296  0.050457  0.004685 -0.010510  0.090073   
876  5166   5 -0.630762  0.055432  0.086061 -0.003899  0.032088  0.010968   
877  5166   6 -0.710593 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
878  5166   9 -0.556295 -0.110296  0.050457  0.004685 -0.010510  0.090073   
879  5167   5 -0.620776  0.055432  0.086061 -0.003899  0.032088  0.010968   
880  5167   6 -0.712227 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
881  5167   9 -0.556295 -0.110296  0.050457  0.004685 -0.010510  0.090073   
882  5169   5 -0.631277  0.055432  0.086061 -0.003899  0.032088  0.010968   
883  5169   6 -0.709893 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
884  5169   9 -0.561545 -0.110296  0.050457  0.004685 -0.010510  0.090073   
885  5170   5 -0.624314  0.055432  0.086061 -0.003899  0.032088  0.010968   
886  5170   6 -0.710813 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
887  5170   9 -0.560627 -0.110296  0.050457  0.004685 -0.010510  0.090073   
888  5171   5 -0.620749  0.055432  0.086061 -0.003899  0.032088  0.010968   
889  5171   6 -0.709258 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
890  5171   9 -0.559132 -0.110296  0.050457  0.004685 -0.010510  0.090073   
891  5172   5 -0.626950  0.055432  0.086061 -0.003899  0.032088  0.010968   
892  5172   6 -0.706296 -0.065669  0.047579 -0.100778  0.006614 -0.008296   
89